In [1]:
!pip install git+https://github.com/myshell-ai/MeloTTS.git >> devnull
!pip install git+https://github.com/myshell-ai/OpenVoice.git >> devnull
!python -m unidic download >> devnull

  Running command git clone --filter=blob:none --quiet https://github.com/myshell-ai/MeloTTS.git /tmp/pip-req-build-q_2jbbnm
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.15.0 requires tensorboard<2.16,>=2.15, but you have tensorboard 2.16.2 which is incompatible.
  Running command git clone --filter=blob:none --quiet https://github.com/myshell-ai/OpenVoice.git /tmp/pip-req-build-37kddejn
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
chex 0.1.86 requires numpy>=1.24.1, but you have numpy 1.22.0 which is incompatible.
cudf-cu12 24.4.1 requires numpy<2.0a0,>=1.23, but you have numpy 1.22.0 which is incompatible.
numexpr 2.10.1 requires numpy>=1.23.0, but you have numpy 1.22.0 which is incompatible.
pandas-stubs 2.0.3.2308

In [2]:
!pip uninstall transformers -y >> devnull
!pip install transformers >> devnull

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
faster-whisper 0.9.0 requires tokenizers<0.15,>=0.13, but you have tokenizers 0.19.1 which is incompatible.
melotts 0.1.2 requires transformers==4.27.4, but you have transformers 4.42.3 which is incompatible.


In [3]:
!pip uninstall numpy -y >> devnull
!pip install numpy==1.25.2 >> devnull

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
myshell-openvoice 0.0.0 requires numpy==1.22.0, but you have numpy 1.25.2 which is incompatible.
faster-whisper 0.9.0 requires tokenizers<0.15,>=0.13, but you have tokenizers 0.19.1 which is incompatible.
melotts 0.1.2 requires transformers==4.27.4, but you have transformers 4.42.3 which is incompatible.
tensorflow 2.15.0 requires tensorboard<2.16,>=2.15, but you have tensorboard 2.16.2 which is incompatible.


In [9]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [4]:
import librosa
from transformers import WhisperProcessor, WhisperForConditionalGeneration, pipeline

import IPython
import os
import torch

from openvoice import se_extractor
from openvoice.api import ToneColorConverter, BaseSpeakerTTS
from melo.api import TTS

Importing the dtw module. When using in academic works please cite:
  T. Giorgino. Computing and Visualizing Dynamic Time Warping Alignments in R: The dtw Package.
  J. Stat. Soft., doi:10.18637/jss.v031.i07.



/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/251 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/231k [00:00<?, ?B/s]

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package cmudict to /root/nltk_data...
[nltk_data]   Unzipping corpora/cmudict.zip.


...

tokenizer_config.json:   0%|          | 0.00/310 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/650 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/248k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/486k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/134 [00:00<?, ?B/s]

In [11]:
!mkdir checkpoints
!unzip /content/drive/MyDrive/checkpoints_1226.zip -d .

Archive:  /content/drive/MyDrive/checkpoints_1226.zip
   creating: ./checkpoints/converter/
  inflating: ./checkpoints/converter/config.json  
  inflating: ./checkpoints/converter/checkpoint.pth  
   creating: ./checkpoints/base_speakers/
   creating: ./checkpoints/base_speakers/ZH/
  inflating: ./checkpoints/base_speakers/ZH/config.json  
  inflating: ./checkpoints/base_speakers/ZH/checkpoint.pth  
  inflating: ./checkpoints/base_speakers/ZH/zh_default_se.pth  
   creating: ./checkpoints/base_speakers/EN/
  inflating: ./checkpoints/base_speakers/EN/config.json  
  inflating: ./checkpoints/base_speakers/EN/en_style_se.pth  
  inflating: ./checkpoints/base_speakers/EN/en_default_se.pth  
  inflating: ./checkpoints/base_speakers/EN/checkpoint.pth  


# ASR with Whisper

In [14]:
# Original voice in Russian:
IPython.display.Audio("/content/voice_ru.m4a")

In [12]:
waveform, sample_rate = librosa.core.load("/content/voice_ru.m4a", sr=16000)

processor = WhisperProcessor.from_pretrained("openai/whisper-tiny", language="russian", task="transcribe")
model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-tiny")

input_features = processor(waveform, sampling_rate=sample_rate, return_tensors="pt")['input_features']

predicted_ids = model.generate(input_features)

transcription = processor.batch_decode(predicted_ids, skip_special_tokens=True)


/usr/local/lib/python3.10/dist-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [6]:
transcription

[' Выбери жизни, выбери работу, выбери карьеру, выбери семью, выберите левизор с большим экраном, выбери стиральную машину, музыкальный центр автомобиль и электрический нож. Выбери здоровый желудок, зубы и медицинскую страховку. Выбери не движимость и аккуратно выплачивай взносы, выбери свой первый дом, выбери друзей, выбери курорты и шикарные чемоданы.']

# Eng-to-Rus translation with Huggingface's model Helsinki-NLP

In [17]:
model_checkpoint = "Helsinki-NLP/opus-mt-ru-en"
translator = pipeline("translation", model=model_checkpoint)
translation = translator(transcription)[0]['translation_text']

/usr/local/lib/python3.10/dist-packages/transformers/models/marian/tokenization_marian.py:175: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


In [18]:
translation

'Choose a life, choose a job, choose a career, choose a family, choose a leftistrator with a big screen, choose a washing machine, a music center car and an electric knife, choose a healthy stomach, teeth and health insurance, choose a non-move and pay your dues carefully, choose your first home, choose your friends, choose resorts and gorgeous suitcases.'

# TTS with OpenVoice

In [23]:
ckpt_base = 'checkpoints/base_speakers/EN'
ckpt_converter = 'checkpoints/converter'
device="cuda:0" if torch.cuda.is_available() else "cpu"
output_dir = 'outputs'

base_speaker_tts = BaseSpeakerTTS(f'{ckpt_base}/config.json', device=device)
base_speaker_tts.load_ckpt(f'{ckpt_base}/checkpoint.pth')

tone_color_converter = ToneColorConverter(f'{ckpt_converter}/config.json', device=device)
tone_color_converter.load_ckpt(f'{ckpt_converter}/checkpoint.pth')

os.makedirs(output_dir, exist_ok=True)

/usr/local/lib/python3.10/dist-packages/torch/nn/utils/weight_norm.py:28: UserWarning: torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.
  warnings.warn("torch.nn.utils.weight_norm is deprecated in favor of torch.nn.utils.parametrizations.weight_norm.")


Loaded checkpoint 'checkpoints/base_speakers/EN/checkpoint.pth'
missing/unexpected keys: [] []


(…)BERP_none0.30_mean1.81_std1.81.model.pkl:   0%|          | 0.00/10.0M [00:00<?, ?B/s]

Loaded checkpoint 'checkpoints/converter/checkpoint.pth'
missing/unexpected keys: [] []


In [24]:
source_se = torch.load(f'{ckpt_base}/en_default_se.pth').to(device)
reference_speaker = '/content/voice_ru.m4a'
target_se, audio_name = se_extractor.get_se(reference_speaker, tone_color_converter, target_dir='processed', vad=True)

OpenVoice version: v1


/usr/local/lib/python3.10/dist-packages/librosa/util/decorators.py:88: UserWarning: PySoundFile failed. Trying audioread instead.
  return f(*args, **kwargs)
/usr/local/lib/python3.10/dist-packages/torch/hub.py:293: UserWarning: You are about to download and run code from an untrusted repository. In a future release, this won't be allowed. To add the repository to your trusted list, change the command to {calling_fn}(..., trust_repo=False) and a command prompt will appear asking for an explicit confirmation of trust, or load(..., trust_repo=True), which will assume that the prompt is to be answered with 'yes'. You can also use load(..., trust_repo='check') which will only prompt for confirmation if the repo is not already trusted. This will eventually be the default behaviour
  warnings.warn(
Downloading: "https://github.com/snakers4/silero-vad/zipball/master" to /root/.cache/torch/hub/master.zip


[(0.11, 64.178), (64.846, 67.26825)]
after vad: dur = 66.48997732426304


/usr/local/lib/python3.10/dist-packages/torch/functional.py:665: UserWarning: stft with return_complex=False is deprecated. In a future pytorch release, stft will return complex tensors for all inputs, and return_complex=False will raise an error.
Note: you can still call torch.view_as_real on the complex output to recover the old return format. (Triggered internally at ../aten/src/ATen/native/SpectralOps.cpp:873.)
  return _VF.stft(input, n_fft, hop_length, win_length, window,  # type: ignore[attr-defined]


In [25]:
src_path = f'/content/voice_en.wav'
base_speaker_tts.tts(translation, src_path, speaker='default', language='English', speed=1.0)

encode_message = "@MyShell"
tone_color_converter.convert(
    audio_src_path=src_path,
    src_se=source_se,
    tgt_se=target_se,
    message=encode_message)

 > Text splitted to sentences.
Choose a life, choose a job, choose a career, choose a family,
choose a leftistrator with a big screen, choose a washing machine,
a music center car and an electric knife, choose a healthy stomach,
teeth and health insurance, choose a non-move and pay your dues carefully,
choose your first home, choose your friends, choose resorts and gorgeous suitcases.
 > ===========================
tʃuz ə laɪf, tʃuz ə dʒɑb, tʃuz ə kəɹɪɹ, tʃuz ə ˈfæməli,
 length:55
 length:55
tʃuz ə leftistɹatoɹ* wɪθ ə bɪg skɹin, tʃuz ə ˈwɑʃɪŋ məˈʃin,
 length:59
 length:59
ə mˈjuzɪk ˈsɛnəɹ kɑɹ ənd ən ɪˈlɛktɹɪk naɪf, tʃuz ə ˈhɛlθi ˈstəmək,
 length:66
 length:66
tiθ ənd hɛɫθ ˌɪnˈʃʊɹəns, tʃuz ə non-move* ənd peɪ jʊɹ duz ˈkɛɹfəli,
 length:67
 length:67
tʃuz jʊɹ fəɹst hoʊm, tʃuz jʊɹ fɹɛndz, tʃuz ɹɪˈzɔɹts ənd ˈgɔɹdʒəs ˈsutˌkeɪsɪz.
 length:77
 length:77


array([ 1.05056597e-03,  1.02478568e-03,  7.44501653e-04, ...,
       -1.02121758e-05,  8.19115376e-05,  1.09028384e-04], dtype=float32)

In [26]:
# Cloned voice in English:
IPython.display.Audio("/content/voice_en.wav")